一些预处理，主要是让eta_schedule中没有空行.

In [10]:
import numpy as np
import pandas as pd

task_df = pd.read_csv("../database/data/eta_task.csv")
schedule_df = pd.read_csv("../database/data/eta_task_schedule.csv")
schedule_df.index = [False] * len(schedule_df)
schedule_df

t                                               path  \
False      9  [(116.4905155, 39.8940372), (116.4883361, 39.8...   
False     11  [(116.4513528, 39.9436912), (116.4493035, 39.9...   
False     13                        [(116.3403829, 39.8001964)]   
False     16  [(116.4788573, 39.8006971), (116.4782662, 39.8...   
False     24  [(116.2505558, 39.9025875), (116.2506942, 39.9...   
...      ...                                                ...   
False  21983  [(116.4299934, 39.8870815), (116.4339522, 39.8...   
False  21984  [(116.4353636, 39.8974426), (116.4365734, 39.8...   
False  21991  [(116.3747006, 39.910886), (116.3716227, 39.91...   
False  21997  [(116.3246973, 39.9371366), (116.3236868, 39.9...   
False  21999  [(116.3022866, 39.9842651), (116.2999059, 39.9...   

                                                   roads  \
False  [37956, 32078, 32074, 34881, 31134, 14277, 220...   
False  [13123, 24303, 24279, 30808, 378, 21507, 35021...   
False                                                 []   
False         [25565, 25577, 25583, 25594, 25563, 25587]   
False  [36347, 36350, 29455, 8271, 20563, 33390, 2056...   
...                                                  ...   
False  [12398, 12458, 12338, 12440, 5171, 23753, 1497...   
False  [12174, 14895, 14966, 14932, 20054, 14949, 149...   
False  [10448, 4554, 4992, 10575, 4990, 10292, 10319,...   
False  [19332, 16122, 14356, 14471, 14496, 14491, 225...   
False  [2827, 22391, 2033, 18873, 4938, 14381, 2830, ...   

                                                 weights  
False  [186.298, 371.614, 225.193, 207.991, 169.829, ...  
False  [174.719, 133.346, 86.412, 145.256, 9.743, 136...  
False                                                 []  
False  [95.739, 113.064, 413.376, 439.087, 456.12, 34...  
False  [11.806, 280.225, 398.223, 373.027, 198.087, 5...  
...                                                  ...  
False  [394.861, 195.611, 51.109, 105.008, 294.605, 9...  
False  [191.571, 41.384, 85.807, 59.815, 43.23, 193.9...  
False  [262.587, 112.787, 126.826, 17.826, 49.909, 90...  
False  [90.173, 230.948, 121.11, 9.134, 34.11, 108.29...  
False  [203.014, 25.277, 13.968, 59.114, 101.046, 174...  

[4400 rows x 4 columns]

In [11]:
for i in range(len(schedule_df)):
    if pd.isnull(schedule_df.iloc[i]['path']):
        schedule_df.iloc[i,1] = str([(-1,-1)])
        schedule_df.iloc[i,2] = str([])
        schedule_df.iloc[i,3] = str([])
schedule_df.to_csv("../database/data/eta_schedule_noempty.csv", index=False)

In [3]:
schedule_df = pd.read_csv("../database/data/eta_schedule_noempty.csv")
for r in schedule_df.iterrows():
    print(r[1][2])

[(116.4905155, 39.8940372), (116.4883361, 39.8940167), (116.4839905, 39.8939508), (116.4839868, 39.895976), (116.4839833, 39.8978465), (116.4839766, 39.8993738), (116.4840506, 39.9033743), (116.4843727, 39.9034865), (116.4846697, 39.9038023), (116.4877327, 39.9038562), (116.4918862, 39.9042203), (116.4920015, 39.9042238), (116.4980915, 39.904497)]
[(116.4513528, 39.9436912), (116.4493035, 39.9436707), (116.4493087, 39.9448699), (116.4493027, 39.945647), (116.4493104, 39.9469533), (116.4493077, 39.9470409), (116.4493021, 39.9482709), (116.4493001, 39.9487227), (116.449299, 39.9489616), (116.4492918, 39.9493996), (116.4507249, 39.9506621), (116.453234, 39.9528726), (116.4534988, 39.9529822), (116.45384, 39.9531234), (116.4537604, 39.9531812), (116.4529884, 39.9536717), (116.4523171, 39.9540982), (116.4511406, 39.9548457), (116.4507311, 39.9551084), (116.4501623, 39.9552979), (116.4499641, 39.9554279), (116.4488182, 39.956176), (116.448104, 39.9566269), (116.4475454, 39.9569986), (116.446

/tmp/ipykernel_917/462451762.py:3: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  print(r[1][2])


进行预测

In [12]:
import numpy as np
import pandas as pd
import torch
from Dataset import ETATaskData, RoadFeatures
from GRU import GRUmodel, GRUBagging
from Utils import *

In [13]:
nbags = 6   # 筛选出来6个

trajSet = ETATaskData("../database/data/eta_schedule_noempty.csv", "../database/data/eta_task.csv", 8)
rawroadfeat = RoadFeatures("./road_features_with_lengths.pkl", "../database/data/road.csv")
base_bagging_dir = "./GRUBagging"
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

GRUs = GRUBagging(rawroadfeat.n_features, device, nbags, is_training=False, params_path=base_bagging_dir).to(device)
fundGRU = GRUmodel(rawroadfeat.n_features, 128, device).eval().to(device)
fundGRU.load_state_dict(torch.load("./GRUonly_result/rawfeature_reg_gru.pt"))

ret = np.zeros((len(trajSet),2))
l = 0
for tids, roadids, tids, start_end_points, start_speeds in trajSet.iter_by_order():
    fund = fundGRU.predict(roadids, start_end_points, start_speeds, rawroadfeat)
    offset = GRUs.predict(roadids, start_speeds, rawroadfeat)
    t = torch.clamp(fund + offset, 2).detach().cpu().numpy()
    ret[l:l+t.shape[0], 0] = tids
    ret[l:l+t.shape[0], 1] = t
    l += t.shape[0]

df = pd.DataFrame(ret, columns=['tid', 'timd'])
df.to_csv("../database/data/eta_answer.csv")

/mnt/f/codes/Python/DataMining/BUAA-DM23/ETA/Dataset.py:136: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  self.road_ids = [ast.literal_eval(r[1][2]) for r in schedule_df.iterrows()]   # 注意iterrows()的结果是一个元组，第一项是idx!
/mnt/f/codes/Python/DataMining/BUAA-DM23/ETA/Dataset.py:138: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  paths = [ast.literal_eval(r[1][1]) for r in schedule_df.iterrows()]
